In [1]:
from __future__ import absolute_import, division, print_function, unicode_literals
# from keras import backend as K
import tensorflow as tf
import keras
import numpy as np
import tensorflow.contrib.eager as tfe
from keras.preprocessing import sequence
from sklearn.model_selection import train_test_split
import time



print(tf.__version__)

Using TensorFlow backend.


1.14.0


In [2]:
tfe.enable_eager_execution(device_policy=tfe.DEVICE_PLACEMENT_SILENT)

In [3]:
imdb = keras.datasets.imdb
num_features = 20000
(train_data, train_labels), (test_data, test_labels) = imdb.load_data(num_words=num_features)
print("Training entries: {}, labels: {}".format(len(train_data), len(train_labels)))

Training entries: 25000, labels: 25000


In [14]:
def loadGloveModel(gloveFile):
    print ("Loading Glove Model")
    f = open(gloveFile,'r')
    model = {}
    for line in f:
        row = line.strip().split(' ')
        word = row[0]
        #print(word)
        embedding = np.array([float(val) for val in row[1:]])
        model[word] = embedding
    print ("Done.",len(model)," words loaded!")
    return model
GLOVE_PATH = 'nlp_adversarial_examples/glove.840B.300d.txt'
glove = loadGloveModel(GLOVE_PATH)

Loading Glove Model
Done. 2196007  words loaded!


In [4]:
# A dictionary mapping words to an integer index
word_index = imdb.get_word_index()

# The first indices are reserved
word_index = {k:(v+3) for k,v in word_index.items()}
word_index["<PAD>"] = 0
word_index["<START>"] = 1
word_index["<UNK>"] = 2  # unknown
word_index["<UNUSED>"] = 3

reverse_word_index = dict([(value, key) for (key, value) in word_index.items()])

def decode_review(text):
    return ' '.join([reverse_word_index.get(i, '?') for i in text])

In [15]:
glove_embedding = np.zeros(shape=(20000,300))
for value in reverse_word_index:
    key = reverse_word_index[value]
    if key in glove:
        glove_embedding[0,:] = glove[key]
    else:
        glove_embedding[0,:] = np.random.uniform(size=(300,))

In [ ]:
print(glove_embedding.shape)

In [5]:
maxlen = 80
x_train = sequence.pad_sequences(train_data, maxlen=maxlen)
x_test = sequence.pad_sequences(test_data, maxlen=maxlen)
print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)

x_train shape: (25000, 80)
x_test shape: (25000, 80)


In [6]:
print(train_labels)

[1 0 0 ... 0 1 0]


In [ ]:
# train_labels = tf.one_hot(train_labels, depth=2)
# test_labels = tf.one_hot(test_labels,depth=2)

In [ ]:
decode_review(x_train[0])

In [11]:
BUFFER_SIZE = len(x_train)
BATCH_SIZE = 32
N_BATCH = BUFFER_SIZE//BATCH_SIZE
embedding_dims = 300
lstm_units = 128

dataset = tf.data.Dataset.from_tensor_slices((x_train, train_labels)).shuffle(BUFFER_SIZE)
dataset = dataset.batch(BATCH_SIZE, drop_remainder=True)

In [7]:
from keras.initializers import Constant

In [16]:
class Classifier(tf.keras.Model):
    def __init__(self,vocab_size,embedding_dim,lstm_units):
        super(Classifier, self).__init__()
        
        self.lstm_units = lstm_units
        self.embedding = tf.keras.layers.Embedding(vocab_size, embedding_dim,embeddings_initializer=Constant(glove_embedding))
        self.lstm = tf.keras.layers.LSTM(lstm_units,dropout=0.2, recurrent_dropout=0.2)
        self.dense = tf.keras.layers.Dense(32,activation=tf.nn.relu)
        self.pred = tf.keras.layers.Dense(1,activation=None)
        

    def call(self, x,is_training):
        x = self.embedding(x)
#         num_samples = tf.shape(x)[0]
#         hidden = tf.zeros((BATCH_SIZE, self.lstm_units))
#         print(self.lstm.get_initial_state(x))
#         print(x)
        o = self.lstm(x)     
#         print(output.shape)
#         o = tf.layers.dropout(o, rate=0.2, training=is_training)
#         o = self.dense(o)
        o = self.pred(o)
#         print(o)
#         o = tf.nn.softmax(o)
#         print(result)
        return o


In [17]:
model = Classifier(num_features, embedding_dims, lstm_units)

In [18]:
optimizer = tf.train.AdamOptimizer()


# [batch_size,class_size]
# [barch_size,]
def loss_function(real, pred):
#     print("real",real,"pred", pred)
#     weights = np.ones(real.shape[0])
#     print(weights)
    pred = tf.reshape(pred, [-1])
    loss_ = tf.losses.sigmoid_cross_entropy(real, pred) 
    print(loss_)
    return loss_

In [ ]:
EPOCHS = 15

for epoch in range(EPOCHS):
    start = time.time()
    total_loss = 0
    for (batch, (inp, targ)) in enumerate(dataset):
        loss = 0
        with tf.GradientTape() as tape:
            output = model(inp,True)
#             print(output)
    
            loss = loss_function(targ, output)
                
        variables = model.trainable_variables
        gradients = tape.gradient(loss, variables)
        optimizer.apply_gradients(zip(gradients, variables))
        
        if batch % 100 == 0:
            print('Epoch {} Batch {} Loss {:.4f}'.format(epoch + 1,
                                                         batch,
                                                         loss))
    # saving (checkpoint) the model every 2 epochs
#     if (epoch + 1) % 2 == 0:
#         checkpoint.save(file_prefix = checkpoint_prefix)
    
#     print('Epoch {} Loss {:.4f}'.format(epoch + 1,
#                                         total_loss / N_BATCH))
#     print('Time taken for 1 epoch {} sec\n'.format(time.time() - start))

In [19]:
checkpoint_prefix = "saved/ckpt/"
root = tf.train.Checkpoint(optimizer=optimizer,
                           model=model,
                           optimizer_step=tf.train.get_or_create_global_step())

# root.save(checkpoint_prefix)

In [20]:
root.restore(tf.train.latest_checkpoint("saved/ckpt/"))

In [22]:
def evaluate_acc(x_test,test_labels):
    test_dataset = tf.data.Dataset.from_tensor_slices((x_test, test_labels)).shuffle(BUFFER_SIZE)
    test_dataset = test_dataset.batch(BATCH_SIZE, drop_remainder=True)
    acc = []
    attack_success = 0
    total = 0
    avg_change = 0
    for (batch, (inp, targ)) in enumerate(test_dataset):
        out = model(inp,False)
        right = 0
        for idx,each in enumerate(out):
            real = targ[idx]
    #         print(inp[idx])
    #         print("actual label:",np.argmax(real),"pred label:",np.argmax(each))
            pred = 0
            real = real.numpy()
            if tf.sigmoid(each).numpy()[0] < 0.5:
                pred = 0
            else:
                pred = 1
            if pred == real:
                right += 1
    #         if np.argmax(each) == np.argmax(real):
    #             right += 1
        batch_acc = right/BATCH_SIZE
        acc.append(batch_acc)
        if batch == 100:
            break
    print(np.mean(acc))
    return np.mean(acc)
evaluate_acc(x_test,test_labels)

0.7926980198019802


0.7926980198019802

In [ ]:
model.trainable_variables[0]

In [ ]:
model.layers

In [ ]:
model.variables

In [23]:
def hotflip_attack(x,gradients,mask,verbose=True):
    embedding = model.embedding
    x_embedding = embedding(x)
    x_grad = gradients.values
    embedding_matrix = embedding.weights[0]
    # grad[x_t]^T * (x_t - x_p) is maximized 
    # The "Hotflip" attack described clearly in https://arxiv.org/abs/1903.06620, 
    # their code I used is here https://github.com/pmichel31415/translate/blob/paul/pytorch_translate/research/adversarial/adversaries/brute_force_adversary.py
    # embedding = [20000,128]  ~ to get x_t
    # x_embedding = [1,80,128] ~ x_t
    # x_grad = [80,128]        ~ grad[x_t]
    # 1 use einsum to compute the grad[x_t]^T * x_p. 
    x_grad = tf.reshape(x_grad,[1,x_grad.shape[0],x_grad.shape[1]])
    product1 = tf.einsum("bij,kj->bik", x_grad, embedding_matrix)
#     print(product1.shape)
    # 2 compute grad[x_t]^T * x_t
    product2 = tf.einsum("bij,bij->bi", x_grad, x_embedding)
#     print(product2.shape)
    product2 = tf.expand_dims(product2,-1)
#     print(product2.shape)
    # 3 we want the maximum of this difference to increase the loss
    neg_dir_dot_grad = -1*(product2 - product1)
#     print(neg_dir_dot_grad.shape)
#     print(product2[0])
#     print("first column",product1[0,:,0])
#     print(neg_dir_dot_grad[0,:,0])
#     print("second column",product1[0,:,1])
#     print(neg_dir_dot_grad[0,:,1])
    
    # 4 maybe normalize it
    # 5 pick the max
    best = tf.argmax(neg_dir_dot_grad,2)
    # Now I have a tensor of size [1,80]. This means for each word i
    # I have a best perturbation generated from the vocab.
    # 6 this step chooses which particular word to attack. The heuristic
    # used here is to simply choose the word with max gradient norm.
    num_of_words = gradients.values.shape[0]
    grads = gradients.values
    grads_norm = tf.einsum("ij,ij->i",grads,grads)
#     print(grads_norm)
    grads_norm = np.einsum("j,j->j",mask,grads_norm)
    which_token = np.argmax(grads_norm)
    if verbose:
        print("perturbed index:",which_token)
        print("perturbed token index:",best.numpy()[0][which_token])
    x_p = best.numpy()[0][which_token]
    new_x = np.array(x)[0]
    new_x[which_token] = x_p
    return best,new_x,which_token


def get_pred(m,x,y,verbose=True):
    output = m(x, False)
    pred = 0
    conf = tf.sigmoid(output).numpy()[0]
    if conf[0] < 0.5:
        pred = 0
    else:
        pred = 1
    if verbose:
        print("\nreal:",y,"pred:",pred, "conf", conf[0],"\n")
    return output,y==pred
    

In [24]:
x = np.array(x_test[1])
y = np.array(test_labels[1])
new_x = np.array(x)
new_x = new_x.reshape((1,80))
new_y = np.array(y)
print(x_test.shape)

def attack(m,x,y,max_perturbed=5,verbose=True):
    success = 0
    if verbose:
        print("\nInitial sentence:")
        print(decode_review(x))
    x =x.reshape((1,80))
    ay = tf.reshape(y, [-1])
    with tf.GradientTape() as tape:
        output,same = get_pred(m,x,y)
    count = 0
    org =x
    mask = np.ones_like(x[0])
    if same:
        while same:
            if verbose:
                print("attack # %d ---------------------------- "%(count))
            with tf.GradientTape() as tape:
                x =x.reshape((1,80))
                output,same = get_pred(m,x,y,False)
                loss = loss_function(ay, output)
                variables = m.trainable_variables
                gradients = tape.gradient(loss, [variables[0]])
                candidates,x2,idx = hotflip_attack(x, gradients[0],mask,verbose=verbose)
            mask[idx] = 0
            if verbose:
                print("perturbed sentences:")
                print(decode_review(x2))
            x = x2
            x =x.reshape((1,80))
            output,same = get_pred(m,x,y,False)
#             print(decode_review(candidates.numpy()[0]))
    #         print(candidates.numpy()[0])
            count += 1
            if count == max_perturbed:
                success = 0
                break
        else:
            print("attack succeed!")
            success = 1
            org = x
    else:
        print("wrong prediction!")
        success = 2
    return success,org
attack(model,x,y)


(25000, 80)

Initial sentence:
wonderfully written script br br i praise robert altman this is one of his many films that deals with unconventional fascinating subject matter this film is disturbing but it's sincere and it's sure to elicit a strong emotional response from the viewer if you want to see an unusual film some might even say bizarre this is worth the time br br unfortunately it's very difficult to find in video stores you may have to buy it off the internet

real: 1 pred: 1 conf 0.99999785 

attack # 0 ---------------------------- 


W0829 13:50:03.864175 4587423168 deprecation.py:323] From /anaconda3/lib/python3.7/site-packages/tensorflow/python/ops/nn_impl.py:180: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


tf.Tensor(2.1283072e-06, shape=(), dtype=float32)
perturbed index: 79
perturbed token index: 18573
perturbed sentences:
wonderfully written script br br i praise robert altman this is one of his many films that deals with unconventional fascinating subject matter this film is disturbing but it's sincere and it's sure to elicit a strong emotional response from the viewer if you want to see an unusual film some might even say bizarre this is worth the time br br unfortunately it's very difficult to find in video stores you may have to buy it off the mocks
attack # 1 ---------------------------- 
tf.Tensor(0.005565976, shape=(), dtype=float32)
perturbed index: 77
perturbed token index: 3179
perturbed sentences:
wonderfully written script br br i praise robert altman this is one of his many films that deals with unconventional fascinating subject matter this film is disturbing but it's sincere and it's sure to elicit a strong emotional response from the viewer if you want to see an unusual

(1, array([[ 1669,   398,   229,    10,    10,    13,  2822,   670,  5304,
            14,     9,    31,     7,    27,   111,   108,    15,  2033,
            19,  7836,  1429,   875,   551,    14,    22,     9,  1193,
            21,    45,  4829,     5,    45,   252,     8, 12508,     6,
           565,   921,  3639,    39,     4,   529,    48,    25,   181,
             8,    67,    35,  1732,    22,    49,   238,    60,   135,
          1162,    14,     9,   290,     4,    58,    10,    10,   472,
            45,    55,   878,     8,   169,    11,   374,  5687,    25,
           203,    28,     8,   818,    12,  3179,     4, 18573]],
       dtype=int32))

In [ ]:
new_x[0][79] = 6836
print(new_x)
print(decode_review(new_x[0]))

In [ ]:
output = model(new_x, False)
pred = 0
conf = tf.sigmoid(output).numpy()[0][0]
if tf.sigmoid(output).numpy()[0] < 0.5:
    pred = 0
else:
    pred = 1
print("\nreal:",new_y,"pred:",pred, "conf", conf,"\n")

# Adversarial Training

### idea 1. do an attack for each review in the training set

In [25]:
def attack_dataset(x_train,train_labels):
    total = 0
    success = 0
    wrong_pred = 0 
    right_pred = 0
    perturbed_idx = []
    perturbed_sen = []
    for idx, x in enumerate(x_train):
        print("data #%d"%(idx))
        total += 1
        newx = np.array(x)
        y = np.array(train_labels[idx])
        o,sentence = attack(model,newx,y)
        if o == 0:
            right_pred += 1
        if o == 1:
            success += 1
            right_pred += 1
            perturbed_idx.append(idx)
            perturbed_sen.append(sentence)
        if o == 2:
            wrong_pred += 1
    print("success attack rate = %f"%(success/(total-wrong_pred)))
    print("prediction score = %f"%(right_pred/total))  
    return perturbed_idx,perturbed_sen
perturbed_idx,perturbed_sen = attack_dataset(x_train,train_labels)

data #0

Initial sentence:
that played the <UNK> of norman and paul they were just brilliant children are often left out of the praising list i think because the stars that play them all grown up are such a big profile for the whole film but these children are amazing and should be praised for what they have done don't you think the whole story was so lovely because it was true and was someone's life after all that was shared with us all

real: 1 pred: 1 conf 0.99898475 

attack # 0 ---------------------------- 
tf.Tensor(0.0010156987, shape=(), dtype=float32)
perturbed index: 79
perturbed token index: 0
perturbed sentences:
that played the <UNK> of norman and paul they were just brilliant children are often left out of the praising list i think because the stars that play them all grown up are such a big profile for the whole film but these children are amazing and should be praised for what they have done don't you think the whole story was so lovely because it was true and was someo

perturbed index: 79
perturbed token index: 14607
perturbed sentences:
up against a wall for an hour then i'd stop and you know why because it felt damn good upon bashing my head in i stuck that damn movie in the <UNK> and watched it burn and that felt better than anything else i've ever done it took american psycho army of darkness and kill bill just to get over that crap i hate you sandler for actually going through with this and ruining a whole day of my executing
attack # 1 ---------------------------- 
tf.Tensor(0.66661984, shape=(), dtype=float32)
perturbed index: 75
perturbed token index: 693
perturbed sentences:
up against a wall for an hour then i'd stop and you know why because it felt damn good upon bashing my head in i stuck that damn movie in the <UNK> and watched it burn and that felt better than anything else i've ever done it took american psycho army of darkness and kill bill just to get over that crap i hate you sandler for actually going through with this and ruining 

KeyboardInterrupt: 

In [26]:
perturbed_idx2,perturbed_sen2 = attack_dataset(x_test,test_labels)

data #0

Initial sentence:
<PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <START> please give this one a miss br br kristy swanson and the rest of the cast rendered terrible performances the show is flat flat flat br br i don't know how michael madison could have allowed this one on his plate he almost seemed to know this wasn't going to work out and his performance was quite lacklustre so all you madison fans give this a miss

real: 0 pred: 1 conf 0.72164017 

wrong prediction!
data #1

Initial sentence:
wonderfully written script br br i praise robert altman this is one of his many films that deals with unconventional fascinating subject matter this film is disturbing but it's sincere and it's sure to elicit a strong emotional response from the viewer if you want to see an unusual film some might even say bizarre this is worth the time br br unfortunately it's very difficult to find in video stores you may have to buy it off the internet

real: 1 pred: 1 conf

tf.Tensor(0.0014613809, shape=(), dtype=float32)
perturbed index: 77
perturbed token index: 437
perturbed sentences:
br the dog story is the very weak vehicle that is used to try and create a story between humans its a terrible storyline there are 3 main musical pieces all of which are rubbish bad songs and dreadful choreography its just an extremely boring film bing has too many words in each sentence and delivers them in an almost irritating manner its not funny ever but its meant to be bing and joan have done much waste than <PAD>
attack # 2 ---------------------------- 
tf.Tensor(0.12865399, shape=(), dtype=float32)
perturbed index: 78
perturbed token index: 0
perturbed sentences:
br the dog story is the very weak vehicle that is used to try and create a story between humans its a terrible storyline there are 3 main musical pieces all of which are rubbish bad songs and dreadful choreography its just an extremely boring film bing has too many words in each sentence and delivers them

tf.Tensor(0.005586605, shape=(), dtype=float32)
perturbed index: 78
perturbed token index: 0
perturbed sentences:
woods looking for fake skulls br br if you do attempt to see this movie you should probably fill up your bathtub and drop your <UNK> in it and be ready to jump in br br this is a must see for anyone who believes there life could not get any worse because this will help you realize there are people out there the makers of this movie who are even more pathetic and are going no where <PAD> <PAD>
attack # 2 ---------------------------- 
tf.Tensor(0.07479205, shape=(), dtype=float32)
perturbed index: 75
perturbed token index: 4758
perturbed sentences:
woods looking for fake skulls br br if you do attempt to see this movie you should probably fill up your bathtub and drop your <UNK> in it and be ready to jump in br br this is a must see for anyone who believes there life could not get any worse because this will help you realize there are people out there the makers of this movie


real: 0 pred: 0 conf 0.0 

attack # 0 ---------------------------- 
tf.Tensor(6.1118848e-09, shape=(), dtype=float32)
perturbed index: 78
perturbed token index: 0
perturbed sentences:
br 5 some scenes were deliberately attempted by the movie makers to be funny and 6 poor and flawed story br br however there are few <UNK> 1 govinda great individual performance br br 2 some scenes are actually quite funny br br 3 <UNK> looks and acting keeps on improving with every film br br 4 rajpal <UNK> don sequences though under utilized but hilarious br br so 4 good points 6 bad ones this one gets <PAD> 10
attack # 1 ---------------------------- 
tf.Tensor(0.026850443, shape=(), dtype=float32)
perturbed index: 79
perturbed token index: 693
perturbed sentences:
br 5 some scenes were deliberately attempted by the movie makers to be funny and 6 poor and flawed story br br however there are few <UNK> 1 govinda great individual performance br br 2 some scenes are actually quite funny br br 3 <UNK> look


real: 1 pred: 1 conf 0.9980254 

attack # 0 ---------------------------- 
tf.Tensor(0.0019766085, shape=(), dtype=float32)
perturbed index: 79
perturbed token index: 13306
perturbed sentences:
mystery a potent mix of comedy and crime this one takes chances where tarantino plays it safe with the hollywood formula the risks don't always pay off one character in one sequence comes off inappropriately silly and falls flat in the lead role thomas jane gives a wonderful and complex performance and two brief appearances by mickey rourke hint at the high potential of this much under and mis used actor here's a director one should keep one's eye unfathomable
attack succeed!
data #23

Initial sentence:
<PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <PAD> <START> eric ability to roll from character to character in this 'one man <UNK> exhibits his true range as a character actor each persona has their own message to convey about truth society class drugs etc this is an absolute must have f

...

tf.Tensor(0.08505129, shape=(), dtype=float32)
perturbed index: 77
perturbed token index: 0
perturbed sentences:
up to a bar look for someone from the outside <UNK> like he is all that and a bag o chips at a barbie and walk away without even being confronted let alone get 'what <UNK> i wasted money on the rental price and am glad i did not purchase the dvd itself br br if this was made by college t a f e students then at least they gave it the old penn try better <PAD> next <PAD>
attack succeed!
data #3144

Initial sentence:
era br br the movie speaks of <UNK> liberation as subtle line of the story i found the development of the story very similar to also written by <UNK> it does rope in some action from the independence struggle and puts in contrast the struggle for indian independence against the silent struggle for <UNK> rights br br a well made movie definitely worth watching <UNK> acting par excellence has handled the story with great care yet another classic from <UNK>

real: 1 p

perturbed index: 79
perturbed token index: 3179
perturbed sentences:
all <UNK> fans macbeth jason connery moved me to tears with his final <UNK> out brief candle out he gave the sphere of moral decay and dark forces a human face which makes it the more interesting helen is a very credible lady macbeth who can be very at times and sometimes she just looks like a naughty girl but deadly in her taste for blood and evil if you love death and decay and lyrics this is the mst3k
attack succeed!
data #3151

Initial sentence:
i still found the movie fascinating and compelling even a completely unnecessarily musical interlude in an army nightclub had me hooked anyone know where i can get a copy of that terrific ray song you don't somebody else will webb plays the toughest dang drill instructor ever and he's under pressure to kick out the deadbeat private owen but by <UNK> he sees a man buried somewhere in that and he's gonna drag him out kicking and screaming great stuff

real: 1 pred: 1 conf 0.


real: 0 pred: 0 conf 0.00018567931 

attack # 0 ---------------------------- 
tf.Tensor(0.00018569655, shape=(), dtype=float32)
perturbed index: 76
perturbed token index: 693
perturbed sentences:
the movie's purpose br br the puppets look really cheesy not in a good way like in the puppet master 80's flicks what did they do to our favorite toys br br the story is lame not interesting and never really explains the sinister origins of the puppets there aren't death scenes like in previous movies and the f x are terrible br br i felt asleep the first time i watched it so i can 7 it for <UNK>
attack succeed!
data #3157

Initial sentence:
is the only thing that the director even tries to make interesting or intense oh and by the way the final scene in the wilderness uh i thought this was in the middle of a run down industrial section of detroit and suddenly we are in the woods the acting isn't terrible in this movie it is just that the directing and writing are atrocious i really enjoy som

tf.Tensor(1.500069e-09, shape=(), dtype=float32)
perturbed index: 79
perturbed token index: 0
perturbed sentences:
made ketchup was the starring role in this movie and would be the only nominee for an award cause the plot actors and anything related to this farce was absolutely horrible and ridiculous i could have made a better horror flick in my backyard within two hours with a hand held camera using grass stuffed <UNK> as the actors <UNK> the acting would have been better don't waste your time or money on this one it's extremely cheesy and <PAD>
attack # 1 ---------------------------- 
tf.Tensor(0.0003609461, shape=(), dtype=float32)
perturbed index: 76
perturbed token index: 3181
perturbed sentences:
made ketchup was the starring role in this movie and would be the only nominee for an award cause the plot actors and anything related to this farce was absolutely horrible and ridiculous i could have made a better horror flick in my backyard within two hours with a hand held camera usi

KeyboardInterrupt: 

In [ ]:
x_train[0]

##### New test data

In [ ]:
maxlen = 80
x_test_adv = sequence.pad_sequences(test_data, maxlen=maxlen)
print('x_train2 shape:', x_test_adv.shape)

In [ ]:
test_adv_labels2 = np.copy(test_labels)

In [ ]:
for idx,sent in zip(perturbed_idx2,perturbed_sen2):
    x_test_adv = np.append(x_test_adv,sent,0)
    test_adv_labels2 = np.append(test_adv_labels2,test_adv_labels2[idx])

###### New train data

In [ ]:
maxlen = 80
x_train2 = sequence.pad_sequences(train_data, maxlen=maxlen)
print('x_train2 shape:', x_train2.shape)

In [ ]:
train_labels2 = np.copy(train_labels)

In [ ]:
for idx,sent in zip(perturbed_idx,perturbed_sen):
    x_train2 = np.append(x_train2,sent,0)
    train_labels2 = np.append(train_labels2,train_labels2[idx])

In [ ]:
print('x_train2 shape:', x_train2.shape)

In [ ]:
train_labels2.shape

In [ ]:
BUFFER_SIZE = len(x_train2)
BATCH_SIZE = 64
N_BATCH = BUFFER_SIZE//BATCH_SIZE
embedding_dims = 64
lstm_units = 100

dataset = tf.data.Dataset.from_tensor_slices((x_train2, train_labels2)).shuffle(BUFFER_SIZE)
dataset = dataset.batch(BATCH_SIZE, drop_remainder=True)

In [ ]:
# better use a new model
EPOCHS = 8

for epoch in range(EPOCHS):
    start = time.time()
    total_loss = 0
    for (batch, (inp, targ)) in enumerate(dataset):
        loss = 0
        with tf.GradientTape() as tape:
            output = model(inp,True)
#             print(output)
    
            loss = loss_function(targ, output)
                
        variables = model.trainable_variables
        gradients = tape.gradient(loss, variables)
        optimizer.apply_gradients(zip(gradients, variables))
        
        if batch % 100 == 0:
            print('Epoch {} Batch {} Loss {:.4f}'.format(epoch + 1,
                                                         batch,
                                                         loss))

### Idea2 taken from Is BERT Really Robust? Use a combination of loss function

In [ ]:
def batch_attack(m,inp,targ):
#     print(inp.shape)
    adv_output = np.zeros((inp.shape[0],inp.shape[1]))
    for idx,(data,label) in enumerate(zip(inp,targ)):
        o,sentence = attack(m,data.numpy(),label.numpy(),verbose=False)
        sentence = np.array(sentence[0])
        adv_output[idx] = sentence
    return adv_output
def evaluate_accuracy(labels,preds):
    total = len(labels)
    counter = 0
    for l,p in zip(labels,preds):
        dummy_l = l.numpy()
        dummy_p = tf.sigmoid(p).numpy()[0]
        if dummy_p >=0.5:
            dummy_p = 1
        else:
            dummy_p = 0
#         print(dummy_l,dummy_p)
        if (dummy_l==dummy_p):
            counter+= 1
    return counter/total

In [ ]:
def combined_loss_function(real,pred,pred_adv,a):
    pred = tf.reshape(pred, [-1])
    pred_adv = tf.reshape(pred_adv, [-1])
    loss_ = tf.losses.sigmoid_cross_entropy(real, pred) 
    loss_adv = tf.losses.sigmoid_cross_entropy(real, pred_adv) 
    print(loss,loss_adv)
    final = tf.add(loss,loss_adv)
    return final

BUFFER_SIZE = len(x_train)
BATCH_SIZE = 64
N_BATCH = BUFFER_SIZE//BATCH_SIZE
embedding_dims = 300
lstm_units = 128

dataset_comb = tf.data.Dataset.from_tensor_slices((x_train, train_labels)).shuffle(BUFFER_SIZE)
dataset_comb = dataset_comb.batch(BATCH_SIZE, drop_remainder=True)
comb_adv_model = Classifier(num_features, embedding_dims, lstm_units)
optimizer = tf.train.AdamOptimizer()

EPOCHS = 12
print("Begin training! Epochs: %d, Num Batches: %d"%(EPOCHS,N_BATCH))

for epoch in range(EPOCHS):
    start = time.time()
    total_loss = 0
    for batch, (inp, targ) in enumerate(dataset_comb):
        print("Epoch: ",epoch,"Batch:",batch)
        loss = 0
        with tf.GradientTape() as tape:
            output = comb_adv_model(inp,True)
            if epoch>=1:
                adv_output = batch_attack(comb_adv_model,inp,targ)
                r = comb_adv_model(adv_output,True)
            if epoch>=1:
                loss = combined_loss_function(targ, output,r,0.5)
            else:
                print("batch accu:",evaluate_accuracy(targ,output))
                loss = loss_function(targ,output)
            print(loss)
        print("------------->>")
                
        variables = comb_adv_model.trainable_variables
        gradients = tape.gradient(loss, variables)
        optimizer.apply_gradients(zip(gradients, variables))
        if batch % 100 == 0:
            print('Epoch {} Batch {} Loss {:.4f}'.format(epoch + 1,
                                                         batch,
                                                         loss))